# Project 1

Building a classification model to predict if a given material is a metal or insulator. Including the prediction of novel two-dimensional insulators. In this task we are disconsidering magnetic materials. 

## Import modules and models

In [77]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
from pymatgen.core.composition import *
import numpy as np
import pandas as pd
import ase.db
from pymatgen.core.composition import *
import numpy as np
import pandas as pd
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import cross_val_score, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, BaggingClassifier
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
import pickle

## Util functions for the models

In [78]:
def evaluate_models(X_train, Y_train, X_test, Y_test):
    # Initialize classifiers
    classifiers = {
        'Logistic Regression': LogisticRegression(),
        'Decision Trees': DecisionTreeClassifier(),
        'Random Forest': RandomForestClassifier(),
        'Gradient Boosting': GradientBoostingClassifier(),
        'Support Vector Machines': SVC()
    }
    
    # Parameters for Grid Search
    params = {
        'Logistic Regression': {'C': [0.1, 1, 10]},
        'Decision Trees': {'criterion': ['gini', 'entropy']},
        'Random Forest': {'n_estimators': [10, 50]},
        'Gradient Boosting': {'n_estimators': [50, 100]},
        'Support Vector Machines': {'C': [0.1, 1, 10]}
    }
    
    # Store results
    results = {}
    
    for name, clf in classifiers.items():
        print(f"Evaluating {name}...")
        
        # Cross Validation
        cv_score = cross_val_score(clf, X_train, Y_train, cv=5).mean()
        
        # Grid Search for Parameter Tuning
        grid_search = GridSearchCV(clf, params[name], cv=5)
        grid_search.fit(X_train, Y_train)
        
        # Bagging
        bagging = BaggingClassifier(clf)
        bagging.fit(X_train, Y_train)
        
        # Test the best estimator from Grid Search
        best_clf = grid_search.best_estimator_
        y_pred = best_clf.predict(X_test)
        
        # Calculate metrics
        accuracy = accuracy_score(Y_test, y_pred)
        precision = precision_score(Y_test, y_pred, average='weighted', zero_division=0)
        recall = recall_score(Y_test, y_pred, average='weighted', zero_division=0)
        f1 = f1_score(Y_test, y_pred, average='weighted', zero_division=0)
        
        # Store results
        results[name] = {
            'CV Score': cv_score,
            'Best Parameters': grid_search.best_params_,
            'Accuracy': accuracy,
            'Precision': precision,
            'Recall': recall,
            'F1 Score': f1
        }
        
        # Print results
        print(f"CV Score: {cv_score}")
        print(f"Best Parameters: {grid_search.best_params_}")
        print(f"Accuracy: {accuracy}")
        print(f"Precision: {precision}")
        print(f"Recall: {recall}")
        print(f"F1 Score: {f1}\n")
        
    return results


def save_best_model(results, X_train, Y_train, metric='F1 Score'):
    # Find the best model based on the given metric
    best_model_name = max(results, key=lambda k: results[k][metric])
    best_model_params = results[best_model_name]['Best Parameters']
    
    # Initialize classifiers
    classifiers = {
        'Logistic Regression': LogisticRegression(),
        'Decision Trees': DecisionTreeClassifier(),
        'Random Forest': RandomForestClassifier(),
        'Gradient Boosting': GradientBoostingClassifier(),
        'Support Vector Machines': SVC()
    }
    
    # Create and train the best model with best parameters
    best_model = classifiers[best_model_name]
    best_model.set_params(**best_model_params)
    best_model.fit(X_train, Y_train)
    
    # Save the best model to a pickle file
    with open(f'{best_model_name}.pkl', 'wb') as f:
        pickle.dump(best_model, f)
        
    print(f"Saved {best_model_name} with {best_model_params} as a pickle file.")
    return best_model

### Get and preparing the data from csv

In [79]:
df_atoms = pd.read_csv('Schleder2019_AtomicTable.csv')

In [80]:
df_atoms.set_index('Element', inplace = True)
dicio = df_atoms.to_dict('index')

In [81]:
data = ase.db.connect('./c2db-2021-06-24.db')
rows = data.select()

In [82]:
# All properties in the atomic table
prop = ['Z',
        'Electronegativity',
        'IonizationPotential',
        'ElectronAffinity',
        'HOMO',
        'LUMO',
        'r_s_orbital',
        'r_p_orbital',
        'r_d_orbital',
        'r_atomic_nonbonded',
        'r_valence_lastorbital',
        'r_covalent',
        'Valence',
        'PeriodicColumn',
        'PeriodicColumn_upto18',
        'NumberUnfilledOrbitals',
        'Polarizability']

In [83]:
# conectado à base de dados 
data = ase.db.connect('./c2db-2021-06-24.db')


#selecionando materiais não metálicos e não magnéticos
rows = data.select(is_magnetic=False)

## Listas que guardarão cada propriedade de cada elemento no composto por vez. ##
lista = []
pesos = []
stch = []
## Dicionário com as features estatísticas de todas as propriedades para cada material##
media_interm = {}

## Lista que guarda cada dicionário de cada material para levar para um dataframe ##
lista_completa = []

target='ehull'
for row in rows:
    
    try:
        comp = Composition(row.formula).as_dict()
        elem = list(comp.items())
        
        ## Acrescentando a fórmula química ##
        media_interm['Material'] = row.formula
        
        ##
        media_interm['ehull'] = row[target]
        
        ## Acrescentando o grupo espacial ##
        media_interm['Space group'] = row.spacegroup
        
        media_interm['Crystal Type'] = row.crystal_type
        
        ## Acrescentando o gap ##
        media_interm['Band gap'] = row.gap
        
        media_interm['stoichiometry'] = row.stoichiometry
    
        for i in prop:
            ## Lista com a propriedade de cada átomo ##
            for m in range(0, len(elem)):
                lista.append(dicio[elem[m][0]][i])
                pesos.append(elem[m][1])
                if (len(elem)==2):
                    stch.append(row.stoichiometry)
        
                
            
            ## Valor médio ##
            media_interm[f'media_{i}'] = np.mean(lista)

    
            ## Média ponderada ##
            avg = np.average(lista,weights=pesos)
            media_interm[f'media_pon_{i}'] = avg
    
            ## Valor máximo e mínimo ##
            max_prop = max(lista)
            min_prop = min(lista)
            media_interm[f'max_{i}'] = max_prop
            media_interm[f'min_{i}'] = min_prop
    
            ## Desvio padrão em relação a média ##
            media_interm[f'desvio_{i}'] = np.std(lista)
    
            ## Desvio padrão em relação a média ponderada ##
            sum_prop = 0
            for j in lista:
                sub2 = (j - avg)**2
                sum_prop = sum_prop + sub2
            media_interm[f'desvio_pon_{i}'] = np.sqrt(sum_prop/len(lista)) 
        
            lista.clear()
            pesos.clear()
        
        lista_completa.append(media_interm.copy())
    except Exception as error:
        print('Error: ', error)

print(set(stch))
    
print(len(lista_completa))
df = pd.DataFrame(lista_completa)
df.sample(20, random_state=100)       

{'AB12', 'AB3', 'A3B4', 'A2B5', 'AB2', 'A2B3', 'AB', 'AB4', 'AB5'}
3227


Material     ehull Space group      Crystal Type  Band gap  \
533       HgH2S2  0.000000          P1         AB2C2-1-a  2.352384   
2104        TlI2  0.120832       P-3m1        AB2-164-bd  0.000000   
2452     Hg3B2O6  0.026377          P1        A2B3C6-1-a  3.521617   
480        TaSe2  0.000000       P-6m2        AB2-187-bi  0.000000   
3223   Hf2Zr2Te8  0.121294          P1          ABC4-1-a  0.165737   
828     Bi2Cu2S4  0.104032      Pmc2_1        ABC2-26-ab  0.135580   
1354  AgSr2Br2O2  0.000000        Amm2    AB2C2D2-38-bce  0.000000   
1689   Na2B2H8O8  0.014137         P-1        ABC4D4-2-i  4.681448   
29      Au2CaF12  0.000000       P-4m2    AB2C12-115-dgl  1.566427   
105     V3C2H2S2  0.364900          Pm     A2B2C2D3-6-ac  0.000000   
3179       MoSTe  0.064536        P3m1        ABC-156-ac  0.992452   
2877        RuO2  0.396039       P-4m2        AB2-115-dg  0.000000   
1583    Os2P2Se6  0.212867          P1          ABC3-1-a  0.000000   
913    Hf4C3H2O2  0.202307       P-3m1  A2B2C3D4-164-acd  0.000000   
1883      Rh2Te2  0.089883       P-3m1          AB-164-d  0.000000   
31      BaF12Sb2  0.000000          P1        AB2C12-1-a  4.965796   
2782        GeI2  0.002626       P-3m1        AB2-164-bd  1.953958   
1067       Re2S2  0.547094      P4/nmm         AB-129-bc  0.000000   
1439      BiMoAs  0.397876        P3m1        ABC-156-ac  0.000000   
411         OsH2  0.420154       P-6m2        AB2-187-bi  0.000000   

     stoichiometry    media_Z  media_pon_Z  max_Z  min_Z  ...  \
533          AB2C2  32.333333    22.800000     80      1  ...   
2104           AB2  67.000000    62.333333     81     53  ...   
2452        A2B3C6  31.000000    27.090909     80      5  ...   
480            AB2  53.500000    47.000000     73     34  ...   
3223          ABC4  54.666667    53.333333     72     40  ...   
828           ABC2  42.666667    36.000000     83     16  ...   
1354       AB2C2D2  32.000000    29.857143     47      8  ...   
1689        ABC4D4   6.250000     5.200000     11      1  ...   
29          AB12C2  36.000000    19.066667     79      9  ...   
105       A2B2C2D3  11.500000    12.777778     23      1  ...   
3179           ABC  36.666667    36.666667     52     16  ...   
2877           AB2  26.000000    20.000000     44      8  ...   
1583          ABC3  41.666667    38.600000     76     15  ...   
913       A2B2C3D4  21.750000    29.454545     72      1  ...   
1883            AB  48.500000    48.500000     52     45  ...   
31          AB12C2  38.666667    17.733333     56      9  ...   
2782           AB2  42.500000    46.000000     53     32  ...   
1067            AB  45.500000    45.500000     75     16  ...   
1439           ABC  52.666667    52.666667     83     33  ...   
411            AB2  38.500000    26.000000     76      1  ...   

      max_NumberUnfilledOrbitals  min_NumberUnfilledOrbitals  \
533                          2.0                         0.0   
2104                         5.0                         1.0   
2452                         5.0                         0.0   
480                          7.0                         2.0   
3223                         8.0                         2.0   
828                          3.0                         1.0   
1354                         2.0                         0.0   
1689                         5.0                         1.0   
29                           1.0                         0.0   
105                          7.0                         1.0   
3179                         6.0                         2.0   
2877                         4.0                         2.0   
1583                         4.0                         2.0   
913                          8.0                         1.0   
1883                         3.0                         2.0   
31                           3.0                         0.0   
2782                         4.0                         1.0   
1067               

### Encoding labeled columns

In [84]:
labelencoder = LabelEncoder()

df['Material'] = labelencoder.fit_transform(df['Material'])
df['Space group'] = labelencoder.fit_transform(df['Space group'])
df['stoichiometry'] = labelencoder.fit_transform(df['stoichiometry'])

In [85]:
y = df['ehull']
X = df.drop(columns=['ehull', 'Crystal Type', 'Band gap']).fillna(0)

### Assertion on zero-values of ehull target

We are using constants because we dont want that the value changes

In [86]:
Y = np.where(np.abs(y) == 0, 1, 0)

### Spliting the data for train and test of the model

In [87]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.25, random_state=40)

In [88]:
results = evaluate_models(X_train, Y_train, X_test, Y_test)

Evaluating Logistic Regression...


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

CV Score: 0.8855371900826446
Best Parameters: {'C': 1}
Accuracy: 0.8996282527881041
Precision: 0.8359463794046482
Recall: 0.8996282527881041
F1 Score: 0.8578817953688007

Evaluating Decision Trees...
CV Score: 0.8417355371900825
Best Parameters: {'criterion': 'gini'}
Accuracy: 0.8748451053283767
Precision: 0.8797910534735679
Recall: 0.8748451053283767
F1 Score: 0.8772305905455938

Evaluating Random Forest...
CV Score: 0.8632231404958677
Best Parameters: {'n_estimators': 10}
Accuracy: 0.8748451053283767
Precision: 0.8408360439900867
Recall: 0.8748451053283767
F1 Score: 0.8556162303955288

Evaluating Gradient Boosting...
CV Score: 0.8892561983471075
Best Parameters: {'n_estimators': 50}
Accuracy: 0.9058240396530359
Precision: 0.8790512262981927
Recall: 0.9058240396530359
F1 Score: 0.8733320974283418

Evaluating Support Vector Machines...
CV Score: 0.8892561983471075
Best Parameters: {'C': 0.1}
Accuracy: 0.9033457249070632
Precision: 0.8160334987078675
Recall: 0.9033457249070632
F1 Score:

In [89]:
model_to_use = save_best_model(results, X_train, Y_train, metric='CV Score')

Saved Gradient Boosting with {'n_estimators': 50} as a pickle file.


## Deploying the model

### Creating a new dataset to predict using the model
Here, we are using the stoichiometries "A2B3", "AB2", "A2B2" instead of only the "A2B3" using in the example of the professor

In [90]:
STCH=['A2B3', 'AB2', 'A2B2']
PROT=['P-3m1','P-6m2','Pmmn','P1',]

TM=['Sc','Ti',]
HL=['F','Cl',]

elem=list(Composition(STCH[0]).as_dict().items())
n=0
new = {}
lista = []

for i in range(len(STCH)):
    elem=list(Composition(STCH[i]).as_dict().items())
    for j in range(len(TM)):
        for k in range(len(HL)):
            for l in range(len(PROT)):
                
                if(int(elem[0][1])==1):
                    if(int(elem[1][1])==1):
                        new['Material']=("%s%s"%(TM[j],HL[k]))
                    else:
                        new['Material']=("%s%s%s"%(TM[j],HL[k],str(int(elem[1][1]))))
                    
                    
                else:
                    if(int(elem[1][1])==1):
                        new['Material']=("%s%s%s%s"%(TM[j],str(int(elem[0][1])),HL[k]))
                    else:
                        new['Material']=("%s%s%s%s"%(TM[j],str(int(elem[0][1])),HL[k],str(int(elem[1][1]))))
                
                
                new['Prototype']=(PROT[l])
                new['stoichiometry'] = STCH[i]
                lista.append(new.copy())
                n+=1
df2 = pd.DataFrame(lista)
df2.sample(10, random_state=100)            
df2

Material Prototype stoichiometry
0     Sc2F3     P-3m1          A2B3
1     Sc2F3     P-6m2          A2B3
2     Sc2F3      Pmmn          A2B3
3     Sc2F3        P1          A2B3
4    Sc2Cl3     P-3m1          A2B3
5    Sc2Cl3     P-6m2          A2B3
6    Sc2Cl3      Pmmn          A2B3
7    Sc2Cl3        P1          A2B3
8     Ti2F3     P-3m1          A2B3
9     Ti2F3     P-6m2          A2B3
10    Ti2F3      Pmmn          A2B3
11    Ti2F3        P1          A2B3
12   Ti2Cl3     P-3m1          A2B3
13   Ti2Cl3     P-6m2          A2B3
14   Ti2Cl3      Pmmn          A2B3
15   Ti2Cl3        P1          A2B3
16     ScF2     P-3m1           AB2
17     ScF2     P-6m2           AB2
18     ScF2      Pmmn           AB2
19     ScF2        P1           AB2
20    ScCl2     P-3m1           AB2
21    ScCl2     P-6m2           AB2
22    ScCl2      Pmmn           AB2
23    ScCl2        P1           AB2
24     TiF2     P-3m1           AB2
25     TiF2     P-6m2           AB2
26     TiF2      Pmmn           AB2
27     TiF2        P1           AB2
28    TiCl2     P-3m1           AB2
29    TiCl2     P-6m2           AB2
30    TiCl2      Pmmn           AB2
31    TiCl2        P1           AB2
32    Sc2F2     P-3m1          A2B2
33    Sc2F2     P-6m2          A2B2
34    Sc2F2      Pmmn          A2B2
35    Sc2F2        P1          A2B2
36   Sc2Cl2     P-3m1          A2B2
37   Sc2Cl2     P-6m2          A2B2
38   Sc2Cl2      Pmmn          A2B2
39   Sc2Cl2        P1          A2B2
40    Ti2F2     P-3m1          A2B2
41    Ti2F2     P-6m2          A2B2
42    Ti2F2      Pmmn          A2B2
43    Ti2F2        P1          A2B2
44   Ti2Cl2     P-3m1          A2B2
45   Ti2Cl2     P-6m2          A2B2
46   Ti2Cl2      Pmmn          A2B2
47   Ti2Cl2        P1          A2B2

In [91]:
## Listas que guardarão cada propriedade de cada elemento no composto por vez. ##
lista = []
pesos = []

## Dicionário com as features estatísticas de todas as propriedades para cada material##
media_interm = {}

## Lista que guarda cada dicionário de cada material para levar para um dataframe ##
lista_completa = []


for i in range(0,100000):
    try:
        formula = df2.iloc[i]['Material']
        comp = Composition(formula).as_dict()
        elem = list(comp.items())
        
        ## Acrescentando a fórmula química ##
        media_interm['Material'] = formula
        
        ## Acrescentando o grupo espacial ##
        media_interm['Space group'] = df2.iloc[i]['Prototype']
        media_interm['stoichiometry'] = df2.iloc[i]['stoichiometry']
    
        for i in prop:
            ## Lista com a propriedade de cada átomo ##
            for m in range(0, len(elem)):
                lista.append(dicio[elem[m][0]][i])
                pesos.append(elem[m][1])
            
            ## Valor médio ##
            media_interm[f'media_{i}'] = np.mean(lista)

    
            ## Média ponderada ##
            avg = np.average(lista,weights=pesos)
            media_interm[f'media_pon_{i}'] = avg
    
            ## Valor máximo e mínimo ##
            max_prop = max(lista)
            min_prop = min(lista)
            media_interm[f'max_{i}'] = max_prop
            media_interm[f'min_{i}'] = min_prop
    
            ## Desvio padrão em relação a média ##
            media_interm[f'desvio_{i}'] = np.std(lista)
    
            ## Desvio padrão em relação a média ponderada ##
            sum_prop = 0
            for j in lista:
                sub2 = (j - avg)**2
                sum_prop = sum_prop + sub2
            media_interm[f'desvio_pon_{i}'] = np.sqrt(sum_prop/len(lista)) 
        
            lista.clear()
            pesos.clear()
        
        lista_completa.append(media_interm.copy())
    except Exception as error:
        print('Error: ', error)


Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional indexer is out-of-bounds
Error:  single positional index

The errors above are caught because we are using a range(0,100000) in the first for-loop. In the example on the github these errors not ocurred due the "Except: pass" clasule. Here, we are using a expcetion treatment.

In [92]:
df = pd.DataFrame(lista_completa)
df.sample(10, random_state=100)

df

Material Space group stoichiometry  media_Z  media_pon_Z  max_Z  min_Z  \
0     Sc2F3       P-3m1          A2B3     15.0    13.800000     21      9   
1     Sc2F3       P-6m2          A2B3     15.0    13.800000     21      9   
2     Sc2F3        Pmmn          A2B3     15.0    13.800000     21      9   
3     Sc2F3          P1          A2B3     15.0    13.800000     21      9   
4    Sc2Cl3       P-3m1          A2B3     19.0    18.600000     21     17   
5    Sc2Cl3       P-6m2          A2B3     19.0    18.600000     21     17   
6    Sc2Cl3        Pmmn          A2B3     19.0    18.600000     21     17   
7    Sc2Cl3          P1          A2B3     19.0    18.600000     21     17   
8     Ti2F3       P-3m1          A2B3     15.5    14.200000     22      9   
9     Ti2F3       P-6m2          A2B3     15.5    14.200000     22      9   
10    Ti2F3        Pmmn          A2B3     15.5    14.200000     22      9   
11    Ti2F3          P1          A2B3     15.5    14.200000     22      9   
12   Ti2Cl3       P-3m1          A2B3     19.5    19.000000     22     17   
13   Ti2Cl3       P-6m2          A2B3     19.5    19.000000     22     17   
14   Ti2Cl3        Pmmn          A2B3     19.5    19.000000     22     17   
15   Ti2Cl3          P1          A2B3     19.5    19.000000     22     17   
16     ScF2       P-3m1           AB2     15.0    13.000000     21      9   
17     ScF2       P-6m2           AB2     15.0    13.000000     21      9   
18     ScF2        Pmmn           AB2     15.0    13.000000     21      9   
19     ScF2          P1           AB2     15.0    13.000000     21      9   
20    ScCl2       P-3m1           AB2     19.0    18.333333     21     17   
21    ScCl2       P-6m2           AB2     19.0    18.333333     21     17   
22    ScCl2        Pmmn           AB2     19.0    18.333333     21     17   
23    ScCl2          P1           AB2     19.0    18.333333     21     17   
24     TiF2       P-3m1           AB2     15.5    13.333333     22      9   
25     TiF2       P-6m2           AB2     15.5    13.333333     22      9   
26     TiF2        Pmmn           AB2     15.5    13.333333     22      9   
27     TiF2          P1           AB2     15.5    13.333333     22      9   
28    TiCl2       P-3m1           AB2     19.5    18.666667     22     17   
29    TiCl2       P-6m2           AB2     19.5    18.666667     22     17   
30    TiCl2        Pmmn           AB2     19.5    18.666667     22     17   
31    TiCl2          P1           AB2     19.5    18.666667     22     17   
32    Sc2F2       P-3m1          A2B2     15.0    15.000000     21      9   
33    Sc2F2       P-6m2          A2B2     15.0    15.000000     21      9   
34    Sc2F2        Pmmn          A2B2     15.0    15.000000     21      9   
35    Sc2F2          P1          A2B2     15.0    15.000000     21      9   
36   Sc2Cl2       P-3m1          A2B2     19.0    19.000000     21     17   
37   Sc2Cl2       P-6m2          A2B2     19.0    19.000000     21     17   
38   Sc2Cl2        Pmmn          A2B2     19.0    19.000000     21     17   
39   Sc2Cl2          P1          A2B2     19.0    19.000000     21     17   
40    Ti2F2       P-3m1          A2B2     15.5    15.500000     22      9   
41    Ti2F2       P-6m2          A2B2     15.5    15.500000     22      9   
42    Ti2F2        Pmmn          A2B2     15.5    15.500000     22      9   
43    Ti2F2          P1          A2B2     15.5    15.500000     22      9   
44   Ti2Cl2       P-3m1          A2B2     19.5    19.500000     22     17   
45   Ti2Cl2       P-6m2          A2B2     19.5    19.500000     22     17   
46   Ti2Cl2        Pmmn          A2B2     19.5    19.500000     22     17   
47   Ti2Cl2          P1          A2B2     19.5    19.500000     22     17   

    desvio_Z  desvio_pon_Z  media_Electronegativity  ...  \
0        6.0      6.118823                     2.67  ...   
1        6.0      6.118823                     2.67  ...   
2        6.0      6.118823                     2.

### Saving the label of materials

In [93]:
materials = df['Material']
spacegroups = df['Space group']
materials

0      Sc2F3
1      Sc2F3
2      Sc2F3
3      Sc2F3
4     Sc2Cl3
5     Sc2Cl3
6     Sc2Cl3
7     Sc2Cl3
8      Ti2F3
9      Ti2F3
10     Ti2F3
11     Ti2F3
12    Ti2Cl3
13    Ti2Cl3
14    Ti2Cl3
15    Ti2Cl3
16      ScF2
17      ScF2
18      ScF2
19      ScF2
20     ScCl2
21     ScCl2
22     ScCl2
23     ScCl2
24      TiF2
25      TiF2
26      TiF2
27      TiF2
28     TiCl2
29     TiCl2
30     TiCl2
31     TiCl2
32     Sc2F2
33     Sc2F2
34     Sc2F2
35     Sc2F2
36    Sc2Cl2
37    Sc2Cl2
38    Sc2Cl2
39    Sc2Cl2
40     Ti2F2
41     Ti2F2
42     Ti2F2
43     Ti2F2
44    Ti2Cl2
45    Ti2Cl2
46    Ti2Cl2
47    Ti2Cl2
Name: Material, dtype: object

### Encoding the labeled columns

In [94]:
df['Material'] = labelencoder.fit_transform(df['Material'])
df['Space group'] = labelencoder.fit_transform(df['Space group'])
df['stoichiometry'] = labelencoder.fit_transform(df['stoichiometry'])

prediction = model_to_use.predict(df)

prediction


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0])

In [95]:
result_prediction = {}

for i in range(0, len(prediction)):
    material = materials[i]
    spacegroup = spacegroups[i]
    result_prediction[f'{material}⁻{spacegroup}'] = prediction[i]

result_prediction

{'Sc2F3⁻P-3m1': 0,
 'Sc2F3⁻P-6m2': 0,
 'Sc2F3⁻Pmmn': 0,
 'Sc2F3⁻P1': 0,
 'Sc2Cl3⁻P-3m1': 0,
 'Sc2Cl3⁻P-6m2': 0,
 'Sc2Cl3⁻Pmmn': 0,
 'Sc2Cl3⁻P1': 0,
 'Ti2F3⁻P-3m1': 0,
 'Ti2F3⁻P-6m2': 0,
 'Ti2F3⁻Pmmn': 0,
 'Ti2F3⁻P1': 0,
 'Ti2Cl3⁻P-3m1': 1,
 'Ti2Cl3⁻P-6m2': 1,
 'Ti2Cl3⁻Pmmn': 1,
 'Ti2Cl3⁻P1': 1,
 'ScF2⁻P-3m1': 0,
 'ScF2⁻P-6m2': 0,
 'ScF2⁻Pmmn': 0,
 'ScF2⁻P1': 0,
 'ScCl2⁻P-3m1': 0,
 'ScCl2⁻P-6m2': 0,
 'ScCl2⁻Pmmn': 0,
 'ScCl2⁻P1': 0,
 'TiF2⁻P-3m1': 0,
 'TiF2⁻P-6m2': 0,
 'TiF2⁻Pmmn': 0,
 'TiF2⁻P1': 0,
 'TiCl2⁻P-3m1': 0,
 'TiCl2⁻P-6m2': 0,
 'TiCl2⁻Pmmn': 0,
 'TiCl2⁻P1': 0,
 'Sc2F2⁻P-3m1': 0,
 'Sc2F2⁻P-6m2': 0,
 'Sc2F2⁻Pmmn': 0,
 'Sc2F2⁻P1': 0,
 'Sc2Cl2⁻P-3m1': 0,
 'Sc2Cl2⁻P-6m2': 0,
 'Sc2Cl2⁻Pmmn': 0,
 'Sc2Cl2⁻P1': 0,
 'Ti2F2⁻P-3m1': 0,
 'Ti2F2⁻P-6m2': 0,
 'Ti2F2⁻Pmmn': 0,
 'Ti2F2⁻P1': 0,
 'Ti2Cl2⁻P-3m1': 0,
 'Ti2Cl2⁻P-6m2': 0,
 'Ti2Cl2⁻Pmmn': 0,
 'Ti2Cl2⁻P1': 0}